In [1]:
import numpy as np
from scipy.io import wavfile
import matplotlib.pyplot as plt

# pynq Overlay
from pynq import Overlay

# audio Codec driver module
from pynq.lib.audio import AudioADAU1761

### Das hier verwendete Design

Das hier verwendete Design *audio_test_v1.bit* basiert vollständig auf dem des *base.bit* welches vom [Pynq Github Repo](https://github.com/Xilinx/PYNQ/tree/master) stammt und auch in den Beispielen aus der [Docs » PYNQ Libraries » Audio](https://pynq.readthedocs.io/en/v2.6.1/pynq_libraries/audio.html) angewand wird. Dabei wurde praktisch nur der für den [ADAU1761 Audio-Codec](https://www.analog.com/en/products/adau1761.html) erstellte Teil des Designs übernommen. Dies dieht lediglich dazu das grundlegende Design und verhalten des Codecs zu verstehen um später darauf aufzubauen und erfüllt den Nutzen als Referenzdesign. <br>
Dementsprechend sind hier auch noch keine Filter integriert. <br>

Die angewanden Funktionen stammen aus dem [pynq.lib.audio Module](https://pynq.readthedocs.io/en/v2.6.1/pynq_package/pynq.lib/pynq.lib.audio.html#pynq-lib-audio).

In [2]:
# overlay laden
ol = Overlay("audio_test_v1.bit")
# Check IP names
ol.ip_dict.keys()

dict_keys(['audio_codec_ctrl_0', 'processing_system7_0'])

#### User-space I/O (UIO)
Ein Linux-Treiber-Modell, das es ermöglicht, auf bestimmte Hardware-Komponenten aus dem Userspace (Python) direkt zuzugreifen, ohne eigenen Kernel-Modul-Treiber schreiben zu müssen. <br>
Die Zuordnung erfolgt beim Booten durch den Kernel-Treiber.

In [3]:
import os
for i in range(4):  # prüfe /dev/uio0 bis /dev/uio3
    try:
        with open(f"/sys/class/uio/uio{i}/name", "r") as f:
            name = f.read().strip()
            print(f"uio{i} → {name}")
    except FileNotFoundError:
        continue

uio0 → audio-codec-ctrl
uio1 → fabric


#### Init des Audiotreibers
Der Treiber für den Audio-Codec wird initialisiert. Es werden die Parameter an den Treiber übergeben.

In [4]:
# Bezeichnung des Audio Codec Kontrollers
audio_description = ol.ip_dict['audio_codec_ctrl_0']
# Übergabe der Bezeichnung an Treiber
pAudio = a = AudioADAU1761(audio_description)
# Eintellen des Audiotreibers
pAudio.configure(sample_rate=48000, iic_index=1, uio_name='audio-codec-ctrl')

#### Eingabe
Es lässt sich einstellen welche Eingabe auf dem Board verwendet werden soll

In [10]:
# einstellen der Lautsärke
pAudio.set_volume(60)

# Einstellen eingang: LineIn
pAudio.select_line_in()

# Einstellen eingang: HP/MIC
# pAudio.select_microphone()

#### .bypass
Aktiviert lediglich einen analogen internen Loop im ADAU1761. Uhmgeht wohl nicht den PL. <br>
-> Könnte also für Realtime Filterung verwendet werden.

In [20]:
# Echtzeitausgabe
Time = 20
pAudio.bypass(seconds=Time)

#### .record / .play
Aufnahme über den ausgewählten Port und Wiederausgabe der im Buffer gespreicherten Aufnahme

In [11]:
# Aufnahme
recTime = 10
pAudio.record(recTime)

In [7]:
# in pAudio.buffer werden die aufnahmen gespreichert
print(pAudio.buffer, type(pAudio.buffer))

[16688844 16688429 16692174 ... 14283229 14335945 14367811] <class 'numpy.ndarray'>


In [12]:
# Buffer ausspielen
pAudio.play()

In [12]:
pAudio.save("test_rec.wav")

In [13]:
from IPython.display import Audio as IPAudio
IPAudio("test_rec.wav")

In [ ]:
# das hier auf keinen fall machen. lässt den Kernel abstürzen !!!!!
recTime = 0.01
Time = 100
while i != Time:
    pAudio.record(recTime)
    pAudio.play()
    i = i + 1

### Echtzeitfiltrierung
#### Probleme mit Echtzeit
##### Ausgangslage
Um das I2S Signal Echtzeitfiltern zu können, muss der Filter zwischen dieses Signal gesetzt werden. In Vivado gibt es I2S Receiver/Transmitter Ip-Cores welche ein I2S Signal annehmen können und als AXI4-Stream ausgeben können und andersrum mit dem Transmitter. Der Filter kann als AXI4-Stream fähiger IP-Core in Matlab erstellt werden und wurde so auch bisher verwendet. Daher könnte der Filter über die I2S Receiver/Transmitter Blöcke an den I2S-Stream angebunden werden.

##### Problem mit I2S Receiver/Transmitter
Der Audio_Codec_Contrtoller Block ist ein vorgefertigter IP-Core aus dem [Pynq Github Repo](https://github.com/Xilinx/PYNQ/tree/master) welcher bei der I2S Übertragung als Master funktioniert und damit *bclk*, *lrclk* und *codec_addr* vorgibt.<br>
Das Problem mit den I2S Receiver/Transmitter Ip-Cores ist, dass diese in dieser Konfiguration als *Slave* arbeiten müssten. Die Funktion wird aber nicht unterstützt. Bedeutet das die IP-Cores nur als *Master* Arbeiten können. [I2S Transmitter and I2S Receiver LogiCORE IP Product Guide](https://docs.amd.com/r/en-US/pg308-i2s/Navigating-Content-by-Design-Process) <br>
Also muss entweder eine andere IP mit Unterstützung als *Slave* her oder dies muss eigens entwickelt werden. <br>
Alternativ könnte auch der Filter IP-Core so umgestaltet werden, dass dieser ein Eingangs I2S-Streams akzeptiert. Dadurch würde sie aber die voraussichtlich die Unterstützung von AXI4-Stream verlieren, wodurch diese auch nicht länger für Digitale Audioquellen wie *.wav* verwendet werden könnten, weshalb derselbe Filter zweimal erstellt werden mussen. <br>
Es gibt eine Möglichkeit die I2S Receiver/Transmitter von *Master* in *Slave* umzuändern laut dieser Quelle: [Audio Processing with the Snickerdoodle](https://www.hackster.io/adam-taylor/audio-processing-with-the-snickerdoodle-727c40). Anderes Board aber änhliche SoC

##### Gleichzeitige Audio-Wiedergabe und -Ausgabe
In dem [Pynq-Z2](https://www.mouser.com/pdfDocs/pynqz2_user_manual_v1_0.pdf) ist ein [ADAU1761 Audio-Codec](https://www.analog.com/en/products/adau1761.html) verbaut. In dem Datenblatt wird nicht expleziet erwähnt ob eine gelcihzeitige Aufnahme und Wiedergabe möglich ist, technisch währe es aber. Wenn die Funktionen aus dem [pynq.lib.audio Module](https://pynq.readthedocs.io/en/v2.6.1/pynq_package/pynq.lib/pynq.lib.audio.html#pynq-lib-audio) verwendet werden wird, ist es nicht möglich. Sobald eine Aufnahme *.record(Time)* gestart wird, wird die Ausgabe *.play()* blockiert bis die Aufnahme vollendet ist. <br>
Mit dem Base-Design, sowie auch diesem hier, ist so direckt die gleichzeitige aufnahme und wiedergabe nicht möglich.

#### Alternative Design Möglichkeiten
Es gibt andere Projekte welche es ermöglichen gelichzeitig Audio Aufzunehmen und Widerzugeben. Inwieweit diese hier verwendet werden können muss noch weiter unteruscht werden. <br>
Hier eine Liste von Projekten: <br>

[Pynq_Z2-Audio](https://github.com/wady101/PYNQ_Z2-Audio/tree/master) <br>
[Audio Processing with the Snickerdoodle](https://www.hackster.io/adam-taylor/audio-processing-with-the-snickerdoodle-727c40)<br>
